In [63]:
from elasticsearch import Elasticsearch
from langchain_groq import ChatGroq

es_client = Elasticsearch(
    hosts="https://512baa73334c4127ade77bc2dfa2ef02.eastus2.azure.elastic-cloud.com:443",
    basic_auth=("elastic", "XRzYOABuG17Yv32UKAFySw41")
)

es_client.ping()

llm = ChatGroq(
    temperature=0,
    model_name="llama-3.1-8b-instant",
    api_key="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",
)

In [64]:
# from elasticsearch import Elasticsearch
# from langchain_groq import ChatGroq

# es_client = Elasticsearch(
#     hosts="https://ae4da19a26f0488b87b8f5f2bb35f565.eastus2.azure.elastic-cloud.com",
#     basic_auth=("elastic", "6AnfGz6hxlSwceSaE5xSsVsd")
# )

# print(es_client.ping())

# llm = ChatGroq(
#     temperature=0,
#     model_name="llama-3.1-8b-instant",
#     api_key="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",
# )


In [9]:
import json
from datetime import datetime
from elasticsearch import Elasticsearch, helpers

filename = 'data.json'
with open(filename, 'r') as json_file:
    loaded_data = json.load(json_file)

`Embedding`

In [31]:
import torch.nn.functional as F
from transformers import AutoModel, AutoTokenizer

model_name_or_path = 'Alibaba-NLP/gte-multilingual-base'

tokenizer = AutoTokenizer.from_pretrained(model_name_or_path)
model = AutoModel.from_pretrained(model_name_or_path, trust_remote_code=True)

A new version of the following files was downloaded from https://huggingface.co/Alibaba-NLP/new-impl:
- configuration.py
. Make sure to double-check they do not contain any added malicious code. To avoid downloading new versions of the code file, you can pin a revision.
A new version of the following files was downloaded from https://huggingface.co/Alibaba-NLP/new-impl:
- modeling.py
. Make sure to double-check they do not contain any added malicious code. To avoid downloading new versions of the code file, you can pin a revision.
Some weights of the model checkpoint at Alibaba-NLP/gte-multilingual-base were not used when initializing NewModel: ['classifier.bias', 'classifier.weight']
- This IS expected if you are initializing NewModel from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing NewModel from the checkpoint of 

In [32]:
input_texts = "Hello"

In [45]:
# Tokenize the input texts
batch_dict = tokenizer(input_texts, max_length=8192, padding=True, truncation=True, return_tensors='pt')

outputs = model(**batch_dict)

dimension=768 # The output dimension of the output embedding, should be in [128, 768]
embeddings = outputs.last_hidden_state[:, 0][:dimension]

print(embeddings.tolist()[0])

[-1.266413688659668, 1.3762707710266113, -0.26227933168411255, -0.28842222690582275, -0.1660219132900238, -0.11616027355194092, 0.30273449420928955, 2.3270883560180664, 1.6070060729980469, -1.3074920177459717, -0.8871795535087585, -0.563014805316925, -3.041653633117676, 0.936244010925293, -1.141948938369751, 1.2805051803588867, 3.1165318489074707, 0.5479347109794617, 0.09357118606567383, 0.7219191789627075, 0.7304482460021973, -0.12229210138320923, -0.7388736605644226, 0.7776566743850708, 0.48307645320892334, 0.8376969695091248, 2.428359270095825, -0.23656481504440308, -1.4089339971542358, -0.36071497201919556, -2.350158214569092, -2.403841495513916, 0.4614515006542206, 0.16254165768623352, 2.23433256149292, -1.1993876695632935, -0.6107953786849976, 0.16196832060813904, -1.2410340309143066, -1.3727078437805176, -1.2269597053527832, -1.5727812051773071, -0.4024810791015625, 1.5310461521148682, -0.39740097522735596, -0.23827219009399414, 0.3686692714691162, 1.7591018676757812, 1.05725753

In [42]:
len(embeddings.tolist()[0])

768

In [46]:
def embedding_creation(tokenizer, model, input_texts):
    batch_dict = tokenizer(
        input_texts, 
        max_length=8192, 
        padding=True, 
        truncation=True, 
        return_tensors='pt'
    )
    outputs = model(**batch_dict)
    dimension = 768
    embeddings = outputs.last_hidden_state[:, 0][:dimension]
    return embeddings.tolist()[0]

doc_list = []

for num, doc in enumerate(loaded_data):
    try:
        dict_doc = { "text": loaded_data[doc] }
        dict_doc["_id"] = num
        dict_doc["heading"] = doc
        embedding_text = embedding_creation(tokenizer, model, loaded_data[doc])
        dict_doc["embedding"] = embedding_text
        doc_list += [dict_doc]

    except json.decoder.JSONDecodeError as err:
        print ("ERROR for num:", num, "-- JSONDecodeError:", err, "for doc:", doc)
        
print ("Dict docs length:", len(doc_list))


Dict docs length: 155


[{'text': 'law no. (12) of 2021 concerning the amendment of some provisions of law no. (28) of 2007 concerning the reorganisation of the zoo and aquarium public institution in al ain we, khalifa bin zayed al nahyan, ruler of abu dhabi having reviewed: • law no. (1) of 1974 concerning the reorganisation of the governmental body in the emirate of abu dhabi and its amendments; • law no. (2) of 1971 concerning the national advisory council, and its amendments; • law no. (28) of 2007 concerning the reorganisation of the zoo and aquarium public institution in al ain, and its amendments; • law no. (8) of 2018 concerning the establishment of the department of culture and tourism; • chairman of the executive council resolution no. (23) of 2018 concerning the additional competencies of the department of culture and tourism; and • based on what was presented to and approved by the executive council, issued the following law: article (1) the definition of the “board of directors” mentioned in arti

In [ ]:
doc_list[0].

In [54]:
resp = helpers.bulk(
    es_client,
    doc_list,
    chunk_size=20, 
    timeout="100m",
    index = "abudhabi-policies-legislations-v2",
)

In [55]:
resp

(155, [])

In [56]:
# question = "Give me some details about Thirty First Investment Zone in the Emirate of Abu Dhabi?"
# question = "Can you explain details about Al Ain Farms for Livestock Production?"
# question = "What is the Private Portfolio and its law details"
question = "Council Resolution No. (4) of 2021"

In [57]:
query_embedding = embedding_creation(tokenizer, model, question)

In [69]:
response = es_client.search(
    index="abudhabi-policies-legislations-v2",
    size=3,
    query={
        "match": {
            "text": question
            }
        },
    knn={
        "field": "embedding",
        "query_vector": query_embedding,
        "k": 5,
        "num_candidates": 10,
    },
    rank={"rrf": {}},
)

In [70]:
summary_text = ""

for hit in response["hits"]["hits"]:
    id = hit["_id"]
    title = hit["_source"]["heading"]
    summary = hit["_source"]["text"]
    summary_text = summary_text + summary
    pretty_output = f"\nID: {id}\nTitle: {title}\nSummary: {summary}"
    print(pretty_output)


ID: 62
Title: executive council resolution no. (46) of 2021 concerning the amendment of some provisions of the chairman of the executive council resolution no. (25) of 2006 concerning the issuance of the
Summary: executive council resolution no. (46) of 2021 concerning the amendment of some provisions of the chairman of the executive council resolution no. (25) of 2006 concerning the issuance of the executive regulations of law no. (23) of 2005 concerning the health insurance scheme in the emirate of abu dhabi the executive council has decided the following: 1. the clause (1) of article (13) of the chairman of the executive council resolution no. (25) of 2006 concerning the issuance of the executive regulations of law no. (23) of 2005 concerning the health insurance scheme in the emirate of abu dhabi, shall be replaced by the following: “the insurance company licensed to operate within the emirate, and wishes to provide health insurance services in accordance with the health insurance

In [71]:
len(summary_text)

7766

In [72]:
import time
from langchain.prompts import PromptTemplate
from langchain_core.output_parsers import StrOutputParser

# Define the prompt template
prompt = PromptTemplate(
    template="""<|begin_of_text|>
    <|start_header_id|>system<|end_header_id|>  
    You are a legal assistant, your task is to answer the user question based on given documents. 

    Legal Documents: {documents}

    Response Instructions:
    1. Formulate a concise, informative response based on the extracted information for the users question.
    2. Reference specific sections or clauses of the documents to support your answer.
    3. Do not answer the question based general knowledge, if the given documents do not have sufficient information to answer the question then send response as "I don't have knowledge to answer your question"
    4. Do not start your response like Based on the provided documents,  here are the details about ...

    User Question: {question}

    <|eot_id|>
    <|start_header_id|>assistant<|end_header_id|>
    """,
    input_variables=["question", "documents"],  # Fixed typo here
)

# Create the question router
question_router = prompt | llm | StrOutputParser()  # Ensure StrOutputParser is instantiated correctly

# Invoke the router with the user's question and legal documents
# question = "Give me some details about Thirty First Investment Zone in the Emirate of Abu Dhabi?"
# question = "What are all the groundwater related future planning in Abu Dhabi?"
response = question_router.invoke(
    {
        "question": question, 
        "documents": summary_text  # Use the corrected variable name
    }
)

print(response)  # Print the response


Executive Council Resolution No. (4) of 2021 concerns the reformation of the Board of Directors of Abu Dhabi Housing Authority. 

According to Article (1) of the resolution, the Board of Directors shall be reformed under the chairmanship of H.E. Falah Mohammed Falah Al-Ahbabi, with the membership of seven individuals, including H.E. Saif Badr Haji Al-Qubaisi as Vice-Chairman. 

The term of the Board's membership is specified in Article (2) as two renewable years. 

This resolution is effective from the date of its issuance and was published in the Official Gazette on 28 February 2021 (corresponding to 16 Rajab 1442 Hijri).


In [1]:
from transformers import AutoTokenizer, AutoModel

tokenizer = AutoTokenizer.from_pretrained('intfloat/multilingual-e5-large')
model = AutoModel.from_pretrained('intfloat/multilingual-e5-large')

c:\Users\tshar\anaconda3\envs\LegalDocRAG\Lib\site-packages\tqdm\auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [9]:
def embedding_creation(tokenizer, model, input_texts):
    batch_dict = tokenizer(
        input_texts, 
        padding=True, 
        truncation=True, 
        return_tensors='pt',
        max_length=1024,
    )
    outputs = model(**batch_dict)
    embeddings = outputs.last_hidden_state[:, 0]
    return embeddings.tolist()[0]

In [10]:
print(len(embedding_creation(tokenizer, model, "Hello")))

1024
